In [33]:
import pickle
import glob
import networkx as nx 
import matplotlib.pyplot as plt

to_classify = ["sample", "domain", "phylum", "class", "order", "family", "genus"]

In [64]:
files = glob.glob('results/ibs/ibs_dicts/*')
taxa_dicts = []
classifier = 'family'

for file in files:
    with open(file, 'rb') as f:
        taxa_dict = pickle.load(f)
        taxa_dicts.append(taxa_dict)
        
# calculate thresholds

# find average value of each
avg_d = {}
total_organisms = {}
num_files = len(files)
num_files_occurred = {}

for file in files:
    with open(file, 'rb') as f:
        taxa_dict = pickle.load(f)
    
    # count total organisms per patient
    organism_count = 0
    for i in taxa_dict[classifier]:
        organism_count += taxa_dict[classifier][i]
        if i not in num_files_occurred:
            num_files_occurred[i] = 1
        else:
            num_files_occurred[i] += 1
    total_organisms[file] = organism_count

    # add normalized data to the total, and divide by number of patients to average
    for i in taxa_dict[classifier]:
        if i not in avg_d:
            avg_d[i] = taxa_dict[classifier][i] / (num_files * organism_count)
        else:
            avg_d[i] += taxa_dict[classifier][i] / (num_files * organism_count)
        
# overall_dict = {}

total_files_per_sample = {}

for file in files:
    with open(file, 'rb') as f:
        taxa_dict = pickle.load(f)
    for i in taxa_dict[classifier]:
        if taxa_dict[classifier][i] / total_organisms[file] < avg_d[i]:
            continue
        else:
            if i not in total_files_per_sample:
                total_files_per_sample[i] = {}
            for j in taxa_dict[classifier]:
                if taxa_dict[classifier][j] / total_organisms[file] >= avg_d[j]:
                    if j not in total_files_per_sample[i]:
                        total_files_per_sample[i][j] = 1
                    else:
                        total_files_per_sample[i][j] += 1   

print(total_files_per_sample)

{'Carsonella': {'Carsonella': 39, 'Halobacteriaceae': 9, 'Flammeovirgaceae': 20, 'Flavobacteriaceae': 30, 'AR17': 23, 'Peptostreptococcaceae': 28, 'Lacipirellulaceae': 15, 'Gemmataceae': 9, 'Desulfurococcaceae': 16, 'Weeksellaceae': 31, 'Chloroplast': 36, 'Gomontiellaceae': 15, 'Desulfobulbaceae': 21, 'Prevotellaceae': 13, 'Chitinophagaceae': 28, 'Thermoproteaceae': 10, 'Bacteriovoracaceae': 23, 'Eggerthellaceae': 15, 'Gemmatimonadaceae': 14, 'Entomoplasmataceae': 26, 'Thermospiraceae': 18, 'Dissulfurirhabdus': 16, 'Salisaetaceae': 13, 'Sterolibacteriaceae': 16, 'Hydrogenothermaceae': 13, 'AR20': 19, 'Sporomusaceae': 27, 'Desulfomicrobiaceae': 15, 'Pseudonocardiales_incertae_sedis': 16, 'Poaceae': 12, 'Anthocerotibacteraceae': 18, 'Actinomycetaceae': 9, 'Rhodospirillaceae': 8, 'Cuniculiplasmataceae': 22, 'AR16': 18, 'Phaselicystidaceae': 13, 'Anaerolineaceae': 7, 'Natrialbaceae': 14, 'Calescibacterium': 14, 'Muribaculaceae': 9, 'Tenuifilaceae': 9, 'Rikenellaceae': 27, 'Haloarculaceae':

In [65]:
# graphing

sum = 0
total = 0

for key in total_files_per_sample:
    for key2 in total_files_per_sample[key]:
        sum += total_files_per_sample[key][key2]
        total +=1

avg_tfs = sum / total

graph = nx.Graph()
used = []
for node in total_files_per_sample:
    if node not in used:
        graph.add_node(node, node_size=0)
    used.append(node)    

for node in total_files_per_sample:
    for other in total_files_per_sample[node]:
        if node != other and total_files_per_sample[node][other] / num_files > avg_tfs / 40: #0.4: IBS
            
            graph.add_edge(node, other, weight = 0.1, color = 'red')

plt.figure(figsize=(15,15), dpi = 600)

nx.draw_circular(graph, node_size = 1, font_size = 8, width = 0.5)

plt.title("Graph of connections between " + classifier)
plt.show()

16.736685440712147


In [14]:
pickle.dump(graph, open("ibs_graph.pkl", "wb"))